# Generate audio from the sequences generated by the model's output

## First we import the required libraries

In [2]:
import numpy as np
import magenta.music as mm
import magenta
import tensorflow
from magenta.protobuf import music_pb2

print ('🎉 Done!')
print (magenta.__version__ )
print (tensorflow.__version__)

🎉 Done!
1.0.2
1.13.1


## Then we load the npy file and generate the NoteSequence

In [3]:
# Load in the npy file
npy_seq = np.load('./outputs/gen_output/gen_output_baselineTFconcat_300epoch.npy')

# Initialize the NoteSequence and the velocity of the sequence
generated_sequence = music_pb2.NoteSequence()
velocity = 80

# Add the tempo of the sequence (Quarter-notes Per Minute)
generated_sequence.tempos.add(qpm=60);

# For 60 QPM, this means that it is 240 sixteenth notes per minute
# Therefore each sixteenth note will take 60/240 (0.25) seconds
note_time_length = 0.25
# note_time_length = 0.3

# Initialize an array for flagging all previously accessed pitches
accessed_flag_arr = np.zeros(npy_seq.shape)

# Now we add the notes to the sequence
# For each timestep
for t,satb in enumerate(npy_seq):
    for voice,pitch in enumerate(satb):
        if np.isfinite(pitch) and accessed_flag_arr[t][voice] == 0:
            start_time = t * note_time_length
            end_time = start_time + note_time_length
            
            iter_t = t
            # if the next pitch is the same with the current one and we haven't reached the end of sequence
            while iter_t != (npy_seq.shape[0]-1) and npy_seq[iter_t][voice] == npy_seq[iter_t+1][voice]:
                # add more time to the end_time
                end_time = end_time + note_time_length

                # move on to the next value in time
                iter_t = iter_t + 1
    
                # flag the future positions in the idx array
                accessed_flag_arr[iter_t][voice] = 1
            
            # flag the current position in the idx array
            accessed_flag_arr[t][voice] = 1
            
            generated_sequence.notes.add(pitch=int(pitch), start_time=start_time, end_time=end_time, velocity=velocity)

# Set the total time
generated_sequence.total_time = end_time

# This is a colab utility method that visualizes a NoteSequence.
mm.plot_sequence(generated_sequence)

# This is a colab utility method that plays a NoteSequence.
mm.play_sequence(generated_sequence,synth=mm.fluidsynth)

Loading BokehJS ...